<a href="https://colab.research.google.com/github/paulodowd/GoogleColab_Simple2DSimulator/blob/main/Sheet1_ObstacleAvoidance.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Introduction

**Before you start**, if you haven't used Python or Google Colab before, there are some exercise sheets to help <a href="https://github.com/paulodowd/GoogleColab_Simple2DSimulator#-info-getting-started">available here</a>.

In this worksheet we are going to write code so that a simulated robot can avoid colliding with obstacles.  The robot will therefore have an observable _behaviour_ of **obstacle avoidance**.  In the image below, we can see a top-down representation of a robot in blue, and an imagined path out of the yellow obstructions.  This is our desirable behaviour.

<p align="center">
<img src="https://github.com/paulodowd/GoogleColab_Simple2DSimulator/blob/main/img/obs_avoidance.png?raw=true" width="50%">
</p>

This means your main exercise is to write a **controller**: a piece of software to make decisions for the robot.  At the bottom of this exercise sheet is an animated output of the simulation.  You'll be able to write your own controller, and then view the behaviour of your robot.  The simulation will indicate a performance score (a **metric**) to help you develop better controllers.  

<p align="center">
<img src="https://github.com/paulodowd/GoogleColab_Simple2DSimulator/blob/main/img/sense_plan_act.png?raw=true" width="70%">
</p>

A useful way to think about this challenge is to write code to repeat three steps: **sense**, **plan** and **act**.   In this exercise sheet, the robot will follow "decisions" which have been declared by you in anticipation of the task.  To state it more generally, we will need to read the sensors to detect the proximity of an object, and then decide how to move the robot - and to write this as code.

<p align="center">
<img src="https://github.com/paulodowd/GoogleColab_Simple2DSimulator/blob/main/img/SimOutput.png?raw=true" width="75%">
</p>

This work sheet is structured with many code cells already written for you.  You will only need to edit "The Controller" and you should only need very simple Python proficiency.  If you want to get started on the exercise straight away, you can navigate to the section **Exercise 1.1: Create your own Robot Controller**.  

**Remember to run all the code cells!** If you do not run all the code cells, you will see an error message.  To make this quicker, you can use the tool bar above and click:
-  `Runtime -> Run All`.  

**To get started**, we first of all need to become familiar with the 2D simulator we are going to use. This exercise sheet has a working 2D simulator embedded within it, and you can review all the code to see how it works.  The next part of the exercise sheet will explain how to interpret the output of the simulator.  Exercise 1.1 then has more specific details on writing your first controller.  

**By the end of this worksheet**, you should have written a simple controller so that your simulated robot can drive around without crashing into obstructions.  You can work to achieve the highest score, and you can compare this with your friends progress.

**In the next worksheet**, we will look at a more difficult challenge - to find an obstruction and then navigate around it at close proximity, whilst still avoiding collisions.



# About the 2D Simulator

This 2D simulator simulates a robot similar to an **e-puck**:
<table><tr><td>
<p align="center">
<img src="https://static.generation-robots.com/9584-product_cover/e-puck-programmable-robot-with-battery.jpg" width="300">
</p>
</td><td>
<p align="center">
<img src="https://www.researchgate.net/profile/Kevin-Nickels-2/publication/289404595/figure/fig4/AS:499790165311491@1496170670005/Overhead-view-of-an-E-Puck-robot-with-the-angles-between-proximity-sensors-labeled-from.png" width="300">
</p>
</td></tr></table>

The robot can move around on two wheels, placed on opposite sides of the robot.  The robot has 8 infra-red proximity sensors which make observations along the red lines in the image above, used to detect obstacles in the environment.  We can program the robot to drive around, turn on the spot, and use it's sensors to avoid colliding with obstacles.  

Our simulated robot looks like the following:

<p align="center">
<img src="https://github.com/paulodowd/GoogleColab_Simple2DSimulator/blob/main/img/WheelSpeeds.png?raw=true">
</p>

Our robot is represented as a blue dot.  A yellow line is used to indicate the forward direction of the robot.  We can control the motion of the robot by providing values between `-1.00` and `+1.00` to the left and right motors (wheels).  We can cause our robot to move forwards like so:

<p align="center">
<img src="https://github.com/paulodowd/GoogleColab_Simple2DSimulator/blob/main/img/MovesForwards.png?raw=true">
</p>

We can cause our robot to move backwards like so:

<p align="center">
<img src="https://github.com/paulodowd/GoogleColab_Simple2DSimulator/blob/main/img/MovesBackwards.png?raw=true">
</p>

We can cause our robot to rotate to the left or right, by writing negative and positive values to each respective motor:

<p align="center">
<img src="https://github.com/paulodowd/GoogleColab_Simple2DSimulator/blob/main/img/Rotates.png?raw=true">
</p>

The robot has 8 sensors, like the e-puck robot.  These are marked by the red dots:

<p align="center">
<img src="https://github.com/paulodowd/GoogleColab_Simple2DSimulator/blob/main/img/Sensors.png?raw=true">
</p>

We can see that the sensors are arranged in the same way as the e-puck. It is important to note that the two sensors facing most forwards are numbers `0` and `7` - this might not be as you expect.  All the sensors are set to have a maximum range of 20cm.  The robot body is set to 10cm diameter.  So this simulated robot can detect obstacles at a distance of two-body-lengths.  

Near the bottom of this worksheet you can see the simulator output proper.  For now, the simulation output looks like the following:

<p align="center">
<img src="https://github.com/paulodowd/GoogleColab_Simple2DSimulator/blob/main/img/SimOutput.png?raw=true" width="75%">
</p>

In the output, you can see:
- a visualisation of when the sensors are detecting objects via the `sensor beam`.  If an object is not detected, a beam is not drawn.  
- obstructions to the robot are drawn as `yellow circles`.  If your robot collides with an obstruction, it will change colour from blue to red.  
- A score, determined by: 
  - your robot will score higher if it can drive in a straight line.  
  - your robot will score higher the faster it moves.
  - your robot will score badly if it collides with an obstacle or does not move.









# Preliminary Code

The following cells contain the code for the elements inside the simulator.  **It is requested that you do not edit any of these cells yet.**  At this stage you do not need to read or understand any of the code in this section.  You can skip ahead to **Exercise 1.1**.  

## Obstacles


In [ ]:
from math import *
import numpy as np

class Obstacle_c:
  
  # Assigns itself a random position within
  # the arena, keeping a set distance from
  # the centre
  def __init__(self, arena_size=200, radius=10, rot=0.0, max_obstacles=1):
    
    self.radius = radius

    # For defined placement
    rot_ang = rot * ((np.pi*2)/max_obstacles)
    rand_dist = np.random.uniform(.35, .65) * (arena_size/2)
    self.x = (arena_size/2) + rand_dist*np.cos(rot_ang)
    self.y = (arena_size/2) + rand_dist*np.sin(rot_ang)
    
    
    # For random placement
    #rand_ang = np.random.random() * (np.pi*2)
    #rand_dist = np.random.uniform(.25, .50) * (arena_size/2)
    #self.x = (arena_size/2) + rand_dist*np.cos(rand_ang)
    #self.y = (arena_size/2) + rand_dist*np.sin(rand_ang)
    

## Proximity Sensors

In [ ]:
from math import *
import numpy as np


#
# The model of the proximity sensor.
#
#
class ProxSensor_c:
  
  # current global xy position of sensor
  x = 0
  y = 0
  theta = 0
  
  # To store the last sensor reading
  reading = 0

  # To set sensor local position around the robot body.
  offset_dist = 0
  offset_angl = 0

  # maximum scan range:
  max_range = 20

  # constructor. by default, sensor sits 10 distance forward
  # and faces 0 radians with respect to robot origin (0,0).
  def __init__(self, offset_dist=5, offset_angl=0):
    self.offset_dist = offset_dist
    self.offset_angl = offset_angl


  def updateGlobalPosition(self, robot_x, robot_y, robot_theta ):

    # Current direction of the sensor is the rotation
    # of the robot body plus the fixed rotation of the 
    # sensor around that same body.
    self.theta = self.offset_angl + robot_theta

    # With the rotation, we now work out where the 
    # sensor sits in cartesian space (x,y) by projecting
    # out by offset_distance.
    # Note, we do this as if the sensor was at origin (0,0)
    sensor_x = (self.offset_dist*np.cos(self.theta))
    sensor_y = (self.offset_dist*np.sin(self.theta))

    # commit new position to memory, translating to the 
    # robots current x,y position.
    self.x = sensor_x + robot_x
    self.y = sensor_y + robot_y

    # If we've reset position, the last sensor reading
    # is now wrong.  
    self.reading = -1

  def scanFor( self, obstruction ):

    # See if the obstruction is within the detection
    # range of the sensor.
    distance = np.sqrt( ((obstruction.x - self.x)**2) + ((obstruction.y - self.y)**2) )
    distance = distance - obstruction.radius

    # if out of range, return error
    # note: real sensors aren't this easy.
    if distance > self.max_range:
      return

    # compute this sensors angle toward the obstruction
    # (e.g. where is the object relative to the sensor?)
    a2o = atan2( ( obstruction.y - self.y), (obstruction.x-self.x ))

    # computer the smallest angle between the line of 
    # sight of the sensor, and the current angle to the
    # obstruction.
    # [insert url here]
    angle_between = atan2( sin(self.theta-a2o),  cos(self.theta-a2o) )
    angle_between = abs( angle_between )
    
    # If the detection is outside of the field of view
    # of the sensor, then we return and do nothing else.
    # This will either leave the reading as -1 (invalid)
    # for the next call.  Or leave the reading as the
    # last valid reading (>-1) it had.
    if angle_between > np.pi/8:
      return

    # If the current reading is -1 then that means
    # this is the first valid reading, and we update
    # the sensor.
    if self.reading < 0:
      self.reading = distance

    # If the sensor already has a valid reading (>-1)
    # then we only store the new reading if it is closer.
    # (closer obstructions block the field of view)
    if self.reading > 0:
      if distance < self.reading:
        self.reading = distance





## The Robot

In [ ]:

from math import *
import numpy as np

#
# The model of the robot.
#
#
class Robot_c:
  
  # We could do something like, manually add 2 sensors  
  #prox_sensors.append( ProxSensor_c(2, np.pi/8) )
  #prox_sensors.append( ProxSensor_c(2, -np.pi/8) )

  def __init__(self, x=50,y=50,theta=np.pi):
    self.x = x
    self.y = y
    self.theta = np.pi# theta
    self.stall = -1 # to check for collisions
    self.score = 0
    self.radius = 5 # 5cm radius
    self.wheel_sep = self.radius*2 # wheel on either side
    self.vl = 0
    self.vr = 0
    
    # This is the body plan of sensors from
    # an e-puck robot! (in radians)
    self.sensor_dirs = [5.986479,
                        5.410521, 
                        4.712389,
                        3.665191, 
                        2.617994, 
                        1.570796,
                        0.8726646, 
                        0.296706,
                        ]

    self.prox_sensors = [] #= ProxSensor_c()
    for i in range(0,8):
      self.prox_sensors.append( ProxSensor_c(self.radius, self.sensor_dirs[i]) )


  def updatePosition( self, vl, vr ):

    if vl > 1.0: 
      vl = 1.0
    if vl < -1.0:
      vl = -1.0
    if vr > 1.0:
      vr = 1.0
    if vr < -1.0:
      vr = -1.0

    # save requested wheel speed for later.
    self.vl = vl
    self.vr = vr

    # clear stall flag, attempt move
    self.stall = -1

    # robot matrix, contributions to motion x,y,theta
    r_matrix = [(vl/2)+(vr/2),0, (vr-vl)/self.wheel_sep]

    # kinematic matrix  
    k_matrix = [
                [ np.cos(self.theta),-np.sin(self.theta),0],
                [ np.sin(self.theta), np.cos(self.theta),0],
                [0,0,1] 
               ]

    result_matrix = np.matmul( k_matrix, r_matrix)

    self.x += result_matrix[0]
    self.y += result_matrix[1]
    self.theta -= result_matrix[2]

    # Once we have updated the robots new global position
    # we should also update the position of its sensor(s)
    for prox_sensor in self.prox_sensors:
      prox_sensor.updateGlobalPosition( self.x, self.y, self.theta )



  # The sensor checks if it is in range to an obstruction,
  # and if yes, calculates the simulated proximity reading.
  # if no, determines and error result.
  def updateSensors(self, obstruction ):

    # for each sensor
    # for each obstruction
    for prox_sensor in self.prox_sensors:
      prox_sensor.scanFor( obstruction ) 

  def collisionCheck(self, obstruction ):
    distance = np.sqrt( ((obstruction.x - self.x)**2) + ((obstruction.y - self.y)**2) )
    distance -= self.radius
    distance -= obstruction.radius
    if distance < 0:
      self.stall = 1
      angle = atan2( obstruction.y - self.y, obstruction.x - self.x)
      self.x += distance * np.cos(angle)
      self.y += distance * np.sin(angle)
    
  def updateScore(self):
    
    # 1 minus the difference between wheel speed
    # to encourage straight line travel.  
    # square root rewards small differences
    diff = np.abs(((self.vl+1) - (self.vr + 1))) * 0.5
    
    if diff > 0.0:
      diff =  1 - np.sqrt( diff )
    else:
      diff = 1 # - 0
    
    
    # Reward motor activation / penalise no movement
    vel = (np.abs(self.vl) + np.abs(self.vr))/2
    
    

    new_score = vel * diff

    

    if self.stall == 1:
      new_score -= 3   

    self.score += new_score
      

# Exercise 1.1: Create your own Obstacle Avoidance Robot Controller

For this exercise you will write your own software controller to produce obstacle avoidance behaviour.  If you feel unsure about programming with Python, there are some extra exercise sheets to help <a href="https://github.com/paulodowd/GoogleColab_Simple2DSimulator#-info-getting-started">available here</a>.  You are also invited to ask for help during the taught sessions with the tutors!

To create obstacle avoidance for our simulated robot, you need to:
1. **sense:** read the proximity sensors
2. **plan:** make a decision about the sensor readings
3. **act:** activate the motors appropriately

In our simulator, **you only need to edit "The Controller" (Controller_c) code cell**, by making changes to the `update(self, robot):` function, the simulator will automatically call and run this function for you.  From within `update(self, robot):`, you can read the sensors, and then return your determined motor speeds for left and right motors (`vl` and `vr` respectively).  This means that your approach to programming your robot should be thought of as a repeating piece of software, which needs to make a new decisions at every update time interval:
<p align="center">
<img src="https://github.com/paulodowd/GoogleColab_Simple2DSimulator/blob/main/img/controller_c.png?raw=true">
</p>

When approaching this problem, there are two basic approaches: you can make a **logical controller**, or a more **mathematical controller**.  



## An example Logical Controller


A logical controller can be written using **selection** statements.  This would mean deciding a series of `if` statements to determine behaviour.  You could write many `if` statements to build up different logical cases of action.  This would mean we would approach the task as a <a href="https://colab.research.google.com/github/paulodowd/GoogleColab_Simple2DSimulator/blob/main/02_Control_Flow.ipynb">control flow</a> problem.  Here is a short example:

```python
class Controller_c:

  # This function is called again and again
  # by the simulator to decide what the robot
  # should do.  
  # Remember to follow a general rule of:
  # 1) sense (read sensors)
  # 2) plan (decide something)
  # 3) act (set motor speeds)
  def update( self, robot ):

    # We will use vl and vr (velocity-left
    # and velocity-right) to store motor 
    # speeds to later send to the motors
    # Motor velocity should be in the range
    # [ -1.0 : +1.0 ]
    vl = 0
    vr = 0

    # Read sensor 0 and store the result
    # Note, use robot.prox_sensors[ n ].reading
    # where n is in the range [ 0 : 7 ] for 
    # the 8 sensors around the body.
    sensor0 = robot.prox_sensors[0].reading

    # Make a decision for motor speeds based
    # on sensor0.  Note, sensors always return
    # a value between [0:20], or -1 if they have
    # not detected something.
    if sensor0 >= 0:
      if sensor0 < 10:

        # We set the left velocity negative, 
        # which would mean backwards
        vl = -0.3

        # We set the right velocity positive,
        # which would mean forwards.
        vr = 0.3

      elif sensor0 < 15:
        # We set the left velocity negative, 
        # which would mean backwards
        vl = -0.1

        # We set the right velocity positive,
        # which would mean forwards.
        vr = 0.1


    # This controller should always return
    # vl, vr
    return vl, vr
```



## An example Mathematical Controller

We can take a more mathematical approach to our controller because we know that the sensors will make a measurement within the range [ 0 : 20 ], and because the motors will accept a command value within the range [ -1.0 : +1.0 ].  The question therefore becomes, how do we transform a sensor signal into a motor signal using <a href="https://colab.research.google.com/github/paulodowd/GoogleColab_Simple2DSimulator/blob/main/01_Operators.ipynb">arithmetic operators</a>?

```python
class Controller_c:

  # This function is called again and again
  # by the simulator to decide what the robot
  # should do.  
  # Remember to follow a general rule of:
  # 1) sense (read sensors)
  # 2) plan (decide something)
  # 3) act (set motor speeds)
  def update( self, robot ):

    # We will use vl and vr (velocity-left
    # and velocity-right) to store motor 
    # speeds to later send to the motors
    # Motor velocity should be in the range
    # [ -1.0 : +1.0 ]
    vl = 0
    vr = 0

    # Read sensor 0 and store the result
    # Note, use robot.prox_sensors[ n ].reading
    # where n is in the range [ 0 : 7 ] for 
    # the 8 sensors around the body.
    sensor0 = robot.prox_sensors[0].reading

    # In this controller, we use our knowledge
    # of the sensor value range to determine a
    # motor speed mathematically.
    # We still need to check the sensor has a 
    # valid reading first (if >= 0 )
    if sensor0 >= 0:    
      vl = sensor0 * 0.1
      vr = sensor0 * -0.1

    # This controller should always return
    # vl, vr
    return vl, vr
```





The below two cells contain the code for the **controller** and the **simulator**.  It might be useful to first go and run the controller and then run the simulator to see what the output looks like. 

Once you have done this, you can edit the controller code cell below to change the behavior of the robot.  You will need to edit only the **controller**.  You are welcome to ask for support if something is confusing or you do not understand.


**You should:**
- run the controller cell, and then the simulator cell, and view the output.
- begin to edit the controller to create your own obstacle avoidance behaviour.  It is useful to ask yourself the questions:

  - how should the robot turn behaviour be effected with respect to the distance of a detected obstacle?
  - which sensors are useful?
  - do you need to use all sensors?
  - is there a useful way to process the sensor distance measurement?

**Tips:**
  - It is useful to split the problem of obstacle avoidance into two seperate problems.  These can then be combined to produce the overall behaviour.
    1. The robot should travel: How fast to drive the robot forwards?
    2. The robot should avoid collision: When to turn the robot?
  - In this exercise, there is not a single "correct" solution.  Instead, we are learning to use the simulator by allowing ourselves to *play*.  
  - If it is taking a long time to compile and execute the simulator, and therefore a long time to develop and test your code, you can change the number of simulated seconds to be smaller.  
    - Within **The 2D Simulator** code cell, look for the variable `numframes = 250` and change this to a smaller value.  This number determines how many simulation cycles are performed.  
  - You can compile all of the code quickly by clicking `Runtime -> Run all`.

## The Controller

The below function is the "controller" called by the robot.  The **controller** is the part of the robot software which must decide how the robot should act.  

A robot needs **you** to write some rules, logic, or intelligence in code so the robot will make autonomous decisions.  This is actually very difficult, because we have to imagine all the different circumstances a robot may encounter. We also need to spend some time to understand how variours parts of the robot work.  

In this controller, we need to read the proximity sensors, make a decision, and then set the motor power.  The below class is a minimal template.  You can edit this controller to produce more interesting and intelligent behaviour from your robot. 

Currently, the sensors will report a distance to an object in the range [ 0 : 20 ], 0 being close and 20 being far, and a value of -1 means that no object was detected.

In [ ]:
#
# Create controller code within def update(self, robot):
#
# The logical controller has been copied here for
# you to make a start.
#
# Make sure you return vl and vr at the end of
# update to move your simulated robot.
#
class Controller_c:
 
  # This function is called again and again
  # by the simulator to decide what the robot
  # should do.  
  # Remember to follow a general rule of:
  # 1) sense (read sensors)
  # 2) plan (decide something)
  # 3) act (set motor speeds)
  def update( self, robot ):
 
    # We will use vl and vr (velocity-left
    # and velocity-right) to store motor 
    # speeds to later send to the motors
    # Motor velocity should be in the range
    # [ -1.0 : +1.0 ]
    vl = 0.2
    vr = 0.2
 
    # Read sensor 0 and store the result
    # Note, use robot.prox_sensors[ n ].reading
    # where n is in the range [ 0 : 7 ] for 
    # the 8 sensors around the body.
    sensor0 = robot.prox_sensors[0].reading
    #sensor1 = robot.prox_sensors[1].reading
    #sensor2 = robot.prox_sensors[2].reading
    # etc...
 
    # Make a decision for motor speeds based
    # on sensor0.  Note, sensors always return
    # a value between [0:20], or -1 if they have
    # not detected something.
    if sensor0 >= 0:
      if sensor0 < 10:
 
        # We set the left velocity negative, 
        # which would mean backwards
        vl = -0.3
 
        # We set the right velocity positive,
        # which would mean forwards.
        vr = 0.3
 
      elif sensor0 < 15:
        # We set the left velocity negative, 
        # which would mean backwards
        vl = -0.1
 
        # We set the right velocity positive,
        # which would mean forwards.
        vr = 0.1
      
 
 
    # This controller should always return
    # vl, vr
    return vl, vr



## The 2D Simulator

The below code is the Simulator itself, which produces an interactive graph as an output. **You do not need to edit any code in this cell.**  You can just click the play icon (> arrow) to compute the simulator output.  It will take about 40seconds to compute the output, depending on how many frames of simulation are set. 

In [ ]:

import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation

%matplotlib inline

# To produce our animated simulation output
from matplotlib import rc
rc('animation', html='jshtml')

# Constants which define the simulator
# We do not need to change these.
numframes = 250
arena_width = 200
num_obstacles = 9
num_sensors = 8


#------------------------------------------------------------
# set up figure and animation
fig = plt.figure(dpi=120)
#fig.subplots_adjust(left=0, right=1, bottom=0, top=1)
ax = fig.add_subplot(111, aspect='equal', autoscale_on=False,
                     xlim=(0, arena_width), ylim=(0, arena_width))


# An instance of our simulated Robot!
# Placed in the centre of the arena.
my_robot = Robot_c(arena_width/2,arena_width/2,np.random.random()*np.pi*2)

gui_robot, = ax.plot([], [], 'bo', ms=my_robot.radius*2)
gui_robot.set_data([], [])
gui_dir, = ax.plot([], [], 'r-', c="yellow")
gui_sensor = ax.plot( *[[],[]]*num_sensors,'r-', c="red")

gui_obstacles, = ax.plot([],[],'bo', ms=24, c="orange")
# A list of obstacles within the space
obstacles = []
obstacles_xy = []
for i in range( num_obstacles ):
  obstacles.append( Obstacle_c( arena_width, 12, i, num_obstacles) )
  obstacles_xy.append( [obstacles[i].x, obstacles[i].y] )

obstacles_xy = np.asarray( obstacles_xy, dtype=float)
gui_obstacles.set_data( obstacles_xy[:,0], obstacles_xy[:,1]  )

# An instance of our controller!
my_controller = Controller_c()


def animate(i):
    
    global ax, fig
    

    # Use controller to set new motor speeds in
    # range [-1.0:+1.0]
    # Note, uses sensor information from prior
    # simulation cycle.
    vl, vr = my_controller.update( my_robot )
    
    # Update robot position, check for collision,
    # then update sensors.
    my_robot.updatePosition(vl, vr)
    for obstacle in obstacles:
      my_robot.collisionCheck( obstacle )
      my_robot.updateSensors( obstacle )

    # Draw the robot, change colour for collision
    gui_robot.set_data(my_robot.x, my_robot.y)
    if my_robot.stall == 1:
      gui_robot.set_color("red")
    else:
      gui_robot.set_color("blue")
    
    # Draw a little indicator so we can see which
    # way the robot is facing
    tx = my_robot.x + (my_robot.radius*1.4*np.cos(my_robot.theta))
    ty = my_robot.y + (my_robot.radius*1.4*np.sin(my_robot.theta))
    gui_dir.set_data( (my_robot.x,tx), (my_robot.y, ty) )


    # Draw the sensor beams
    for i in range(8):
      prox_sensor = my_robot.prox_sensors[i]
      ox = prox_sensor.x
      oy = prox_sensor.y
      if prox_sensor.reading > 0:
        tx = prox_sensor.x + prox_sensor.reading * np.cos( prox_sensor.theta)
        ty = prox_sensor.y + prox_sensor.reading * np.sin( prox_sensor.theta)
      else:
        tx = prox_sensor.x + np.cos( prox_sensor.theta)
        ty = prox_sensor.y + np.sin( prox_sensor.theta)

      gui_sensor[i].set_data( (ox,tx), (oy, ty) )
    
    # Update the current score in the title!
    my_robot.updateScore()
    ax.set_title('Score: {0:f}'.format( my_robot.score ))
    
    return gui_robot, 

plt.close()
ani = animation.FuncAnimation(fig, animate, frames=numframes, interval=10, blit=True)
ani


#plt.show()

# Exercise 1.2: Evaluating your Controller

By now you should have a controller for your robot which allows it to successfully navigate without colliding with obstacles.  It can be tricky to get good performance!  

Even when we think we have good performance, usually we do not know how good a solution is until we compare it against something else.  In this case, we can compare our solution against a friend or peer.  

- Talk to someone near you.  How does your score compare to your peers?
- What techniques have your peers used, compared to you?
- With your current controller, create a list of the different scores your robot achieves.
  - Run the simulator 20 times and record the score achieved for each.  You can write the scores into the code cell below.
  - Plot your result scores as a graph.  You can find some help on using matplotlib to make graphs <a href="https://colab.research.google.com/github/ageron/handson-ml2/blob/master/tools_matplotlib.ipynb#scrollTo=KnBYqyxaOLt1">here</a>
  - Exchange your data with a peer, and plot your results against theirs on the same graph.
    - investigate to see if you can render a box-and-whisker plot.
    - who has the better controller?
  - How reliable would you say your controller is?
    - If you ran the simulator 100 times, how many times would your robot crash?
    - What do you think are the primary causes of any variation?



In [ ]:
# You can use this code cell to try out code or to 
# plot your own graphs with data you collect.

my_results = [0,0,0,0,0,0]